## Prelude to Hughes & Hase Chapter 8, A Bad model

In Part B of the Prelude to Chapter 8, we looked at the expected distribution 
of values of $\chi^2$ for the fit of a straight line to 5 data points.  In this part we
repeat exactly the same process, but the model is an exponential decay, and 
we fit the model to a larger number of data points that don't fit the model as well.

Ned Ladd, March 2022

In [ ]:
import numpy as np
from scipy import stats
from scipy import optimize

import matplotlib as mpl
import matplotlib.pyplot as plt

In [ ]:
# Following is an Ipython magic command that puts figures in notebook.
%matplotlib notebook
        
# M.L. modifications of matplotlib defaults
# Changes can also be put in matplotlibrc file, 
# or effected using mpl.rcParams[]
mpl.style.use('classic') 
plt.rc('figure', figsize = (6, 4.5))  # Reduces overall size of figures
plt.rc('axes', labelsize=16, titlesize=14)
plt.rc('figure', autolayout = True)   # Adjusts supblot parameters for new size

#### Functions
Remember:
$$
\chi^2 = \sum_i\frac{\left(y(x_i) - y_i\right)^2}{\alpha_i^2}
$$

In [ ]:
def f(x,q,r,s):
    '''Simple exponential decay function (with offset); nonlinear
    in the fit parameteres q, r, and s.'''
    return q*np.exp(-r*x) + s

def chi2(x,y,u,q,r,s):
    '''Chisquare as a function of data (x, y, and yerr=u), and model 
    parameters q, r, and s'''
    return np.sum((y - f(x,q,r,s))**2/u**2)

## Data Set III

In [ ]:
data = np.array([[0.        , 7.46129812, 0.4       ],
       [0.2       , 5.85452157, 0.4       ],
       [0.4       , 7.07717576, 0.4       ],
       [0.6       , 5.4736062 , 0.4       ],
       [0.8       , 3.8904504 , 0.4       ],
       [1.        , 4.79926158, 0.4       ],
       [1.2       , 4.55971739, 0.4       ],
       [1.4       , 3.60873722, 0.4       ],
       [1.6       , 2.86732949, 0.4       ],
       [1.8       , 2.84260122, 0.4       ],
       [2.        , 2.13946228, 0.4       ],
       [2.2       , 2.22060587, 0.4       ],
       [2.4       , 1.63133617, 0.4       ],
       [2.6       , 2.46693153, 0.4       ],
       [2.8       , 2.32689348, 0.4       ],
       [3.        , 1.5128004 , 0.4       ],
       [3.2       , 1.20809552, 0.4       ],
       [3.4       , 1.43849374, 0.4       ],
       [3.6       , 1.36242689, 0.4       ],
       [3.8       , 2.13797785, 0.4       ],
       [4.        , 1.72819865, 0.4       ]])

x, y, u = data.T

In [ ]:
plt.figure()
plt.title('Data set #2')
plt.xlabel('$x$')
plt.ylabel('$y$')
plt.xlim(-0.5,4.5) 
plt.ylim(0,9)
plt.errorbar(x,y,yerr=u,fmt='o');

### Find best-fit parameters ("old business")

In [ ]:
p0 = 5, 1, 1   # Initial estimates of q, r, and s
popt, pcov = optimize.curve_fit(f, x, y, p0, sigma=u, absolute_sigma=True)
chi2_data = chi2(x,y,u,*popt)
print("chi2_data =", chi2_data)

In [ ]:
xc = np.linspace(0,6,201) # quasi-continuous set of x's for function plot
plt.figure()
plt.title("Data set #2 with best fit function")
plt.xlabel('$x$')
plt.ylabel('$y$')
plt.axhline(0, color='magenta')
plt.xlim(-0.5,4.5)  # Pad x-range on plot
plt.errorbar(x, y, yerr=u, fmt='o');
plt.plot(xc ,f(xc, *popt));

#### Normalized residuals

In [ ]:
plt.figure()
plt.axhline(0,color='magenta')
plt.xlabel('$x$')
plt.ylabel('normalized residuals')
plt.title('Data set #2: normalized residuals')
plt.grid(True)
plt.errorbar(x,(f(x,*popt)-y)/u,1,fmt='o')
plt.xlim(-0.5,5.5);

### What confidence can we have in the model? ("new business")

Normalized residuals look ok according to qualitative assessments 
mentioned, so precede to more quantitative measures.

1. <b>Assume the model is correct</b>, and that any deviations 
from the model are due to the fact that data is the result of
random sampling from normal probability distributions characterized by the 
known standard errors of the data points.  This assumption is called
the <b>null hypothesis</b>.
2. <b>Generate many simulated data sets</b> based on the model, best-fit parameters, and uncertainties. (Use same values for $x_i$).
3. <b>Fit each of the simulated data sets</b> and store the values of 
$\chi^2$ in an array.
4. <b>Examine the histogram of simulated values of $\chi^2$.</b>
Where does the value of $\chi^2_{\text{min}}$ from the fit to the 
original data fall within the histogram?  What's the probability of 
getting values of $\chi^2$ from the simulated data sets 
that are greater than the value given by the data that was actually measured? 
In other words, is our value of $\chi^2_{\text{min}}$ a reasonable result from the model
and the fluctuations we expect in our data?

#### Simulation

In [ ]:
n_sim = 10000               # Number of data sets to simulate
count = 0

chi2_sim = np.zeros(n_sim)  # Array for chisq valuesfrom simulated sets

for i in range(n_sim):
    y_sim = stats.norm.rvs(f(x,*popt), u)  # Generate simulated data set
    popt_sim, pcov_sim = optimize.curve_fit(f, x, y_sim, popt, sigma=u, absolute_sigma=True)
    a = chi2(x,y_sim,u,*popt_sim)   # Calculate chisq for simulated data
    chi2_sim[i] = a                 # store value of chisq
    if a > chi2_data:               # increment counter
        count += 1

In [ ]:
print("% of simulated sets with chisq larger than that from orig. data =", 100*count/n_sim)
mean  = np.mean(chi2_sim)
sigma = np.sqrt(np.var(chi2_sim))
print("mean of simulated values of chisq =", mean)
print("std of simulated values of chisq =", sigma)

#### Histogram of results from simulation

In [ ]:
nbins = 25  # number of bis
low = 0     # lower limit for histogram 
#high = mean + 5*sigma
high = 50   # upper limit for histogram

plt.figure()
plt.xlabel("$\chi^2$")
plt.ylabel("occurrences")
plt.title("Histogram; equal sized bins")
out = plt.hist(chi2_sim, nbins, [low,high], label="$\chi^2$ from sim. data")
#out[0],out[1]   # occurrences and bin boundaries (for use in future)

plt.axvline(chi2_data, label='$\chi^2 = 34.7$')
plt.legend();

### Discussion

Again, the histogram gives 
a <i>probability distribution</i> for values $\chi^2$ that 
minimize data sets consistent with the model and uncertainties.
With more data points, the probability distribution is 
more symmetric than that in Part A.

Again, the value of $\chi^2$ obtained
by fitting the original data is in the range of values we expect from 
the model and uncertainties.  To be more quantitative, 
there is a 1% chance of getting a value of $\chi^2$ that 
is 34.7 or bigger, so it's not very reasonable at all to expect a value 
of about 34.7.

<b>Therefore, you should be very suspicious of the exponential decay model for these data, based on the value of 
 $\chi^2$.</b>
 
If you end up in a situation like this, there are two possibilities to consider:
<Ul>
    <li> The model you're trying to fit doesn't adequately explain the data. Perhaps you need to consider a more sophisticated version, or even some different physical understanding of the situation that produced these data. 
    <li> Your uncertainties are too small, and don't adequately represent the variation that one might expect betweeen the (assumed correct) model and the data you measured. You might want to re-examine your measurement technique and make sure that you have properly characterized its measuring capacity. 
 

### The $\chi^2$ Distribution

You don't need to simulate the distribution of $\chi^2$ values each time you do a fit, because the functional form for this distribution is well-known. It's characterized by the number of <b>degrees of freedom</b> in your fitting process. In nearly all cases, you can determine the number of degrees of freedom by subtracting the number of parameters in your model (in this case, 3) from the number of datapoints to be fit (21). 

Then, we can use the CDF for this distribution to determine the probability of finding a value of $\chi^2$ less than or equal to our determined $\chi^2_{min}$. Or, as is more useful in this case, 1 - CDF will give us the probability of finding a $\chi^2$ greater than our value of $\chi^2_{min}$

In [ ]:
prob = 1 - stats.chi2.cdf(chi2_data,18)
print("Probability that we would find chi-square larger than what we found:",prob)

#### Version details
`version_information` is from J.R. Johansson (jrjohansson at gmail.com); see <a href='http://nbviewer.jupyter.org/github/jrjohansson/scientific-python-lectures/blob/master/Lecture-0-Scientific-Computing-with-Python.ipynb'>Introduction to scientific computing with Python</a> for more information and instructions for package installation.

`version_information` is installed on the linux network at Bucknell

In [ ]:
%load_ext version_information

In [ ]:
version_information numpy, scipy, matplotlib